# Bounding BOX Prediction on Engineering Materials Dataset using DETR

-  In this notebook, I have used Deep Learning DETR model to train and  predict bounding boxes for engineering materials dataset
- 

## Define useful boilerplate functions

Adapted from:
-   https://colab.research.google.com/github/facebookresearch/detr/blob/colab/notebooks/detr_attention.ipynb

In [1]:
# Mount the google drive
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
!pip install -U torch==1.7.0
!pip install -U torchvision==0.8.1 
!pip install -U torchtext==0.8.0

     |████████████████████████████████| 776.7 MB 4.5 kB/s 
  Attempting uninstall: torch
    Found existing installation: torch 1.9.0+cu102
    Uninstalling torch-1.9.0+cu102:
      Successfully uninstalled torch-1.9.0+cu102
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
torchvision 0.10.0+cu102 requires torch==1.9.0, but you have torch 1.7.0 which is incompatible.
torchtext 0.10.0 requires torch==1.9.0, but you have torch 1.7.0 which is incompatible.
     |████████████████████████████████| 12.7 MB 4.5 MB/s 
  Attempting uninstall: torchvision
    Found existing installation: torchvision 0.10.0+cu102
    Uninstalling torchvision-0.10.0+cu102:
      Successfully uninstalled torchvision-0.10.0+cu102
     |████████████████████████████████| 6.9 MB 4.5 MB/s 
  Attempting uninstall: torchtext
    Found existing installation: torchtext 0.10.0
    Uninstalling torchte

In [3]:
import torch, torchvision
print(torch.__version__, torchvision.__version__, torch.cuda.is_available())

torch.set_grad_enabled(False);

1.7.0 0.8.1 True


## Copy all the processed datasets and annotations

In [4]:
! cp  '/content/drive/My Drive/eva6_capstone_final/engineering_processed_dataset_valid_annotation.zip' .
! cp '/content/drive/My Drive/eva6_capstone_final/engineering_processed_dataset_train_part1.zip' .
! cp '/content/drive/My Drive/eva6_capstone_final/engineering_processed_dataset_train_part2.zip' .
! cp '/content/drive/My Drive/eva6_capstone_final/engineering_processed_dataset_train_part3_1.zip' .
! cp '/content/drive/My Drive/eva6_capstone_final/engineering_processed_dataset_train_part3_2.zip' .
! cp '/content/drive/My Drive/eva6_capstone_final/engineering_processed_dataset_train_part4_1.tar.gz' .
! cp '/content/drive/My Drive/eva6_capstone_final/engineering_processed_dataset_train_part4_2.tar.gz' .


In [5]:
! unzip -q engineering_processed_dataset_valid_annotation.zip
! unzip -q engineering_processed_dataset_train_part1.zip
! unzip -q engineering_processed_dataset_train_part2.zip
! unzip -q engineering_processed_dataset_train_part3_1.zip
! unzip -q engineering_processed_dataset_train_part3_2.zip


In [6]:
! tar -zxvf engineering_processed_dataset_train_part4_1.tar.gz  > /dev/null
! tar -zxvf engineering_processed_dataset_train_part4_2.tar.gz  > /dev/null

In [7]:
!mkdir -p /content/data/custom/
!mv /content/annotations /content/data/custom/
!mv /content/train2017 /content/data/custom/
!mv /content/val2017 /content/data/custom/

In [8]:
!ls -l /content/data/custom/

total 640
drwxr-xr-x 2 root   root     4096 Sep  8 01:11 annotations
drwxrwx--- 2 197609 197609 602112 Sep  8 12:34 train2017
drwxr-xr-x 2 root   root    45056 Sep  8 01:10 val2017


In [9]:
!ls -l /content/data/custom/val2017

total 551796
-rw-r--r-- 1 root root   34222 Sep  8 01:05  aac_blocks_110.jpg
-rw-r--r-- 1 root root   12795 Sep  8 01:05  aac_blocks_122.jpg
-rw-r--r-- 1 root root   30181 Sep  8 01:05  aac_blocks_128.jpg
-rw-r--r-- 1 root root   61180 Sep  8 01:05  aac_blocks_198.jpg
-rw-r--r-- 1 root root  261856 Sep  8 01:05  aac_blocks_209.jpg
-rw-r--r-- 1 root root    9993 Sep  8 01:05  aac_blocks_239.jpg
-rw-r--r-- 1 root root    5066 Sep  8 01:05  adhesives_279.jpg
-rw-r--r-- 1 root root   10189 Sep  8 01:05  adhesives_288.jpg
-rw-r--r-- 1 root root   12908 Sep  8 01:05  adhesives_315.jpg
-rw-r--r-- 1 root root   14344 Sep  8 01:05  adhesives_332.jpg
-rw-r--r-- 1 root root   85357 Sep  8 01:05  adhesives_334.jpg
-rw-r--r-- 1 root root  106416 Sep  8 01:05  adhesives_350.jpg
-rw-r--r-- 1 root root   99276 Sep  8 01:05  adhesives_356.jpg
-rw-r--r-- 1 root root  136399 Sep  8 01:05  adhesives_360.jpg
-rw-r--r-- 1 root root   52940 Sep  8 01:05  ahus_375.jpg
-rw-r--r-- 1 root root    6471 Sep  8 01:

## Write all the common functions

In [10]:
import torchvision.transforms as T

# standard PyTorch mean-std input image normalization
transform = T.Compose([
    T.Resize(800),
    T.ToTensor(),
    T.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
])

# for output bounding box post-processing
def box_cxcywh_to_xyxy(x):
    x_c, y_c, w, h = x.unbind(1)
    b = [(x_c - 0.5 * w), (y_c - 0.5 * h),
         (x_c + 0.5 * w), (y_c + 0.5 * h)]
    return torch.stack(b, dim=1)

def rescale_bboxes(out_bbox, size):
    img_w, img_h = size
    b = box_cxcywh_to_xyxy(out_bbox)
    b = b * torch.tensor([img_w, img_h, img_w, img_h], dtype=torch.float32)
    return b

In [11]:
def filter_bboxes_from_outputs(outputs,
                               threshold=0.7):
  
  # keep only predictions with confidence above threshold
  probas = outputs['pred_logits'].softmax(-1)[0, :, :-1]
  keep = probas.max(-1).values > threshold

  probas_to_keep = probas[keep]

  # convert boxes from [0; 1] to image scales
  bboxes_scaled = rescale_bboxes(outputs['pred_boxes'][0, keep], im.size)
  
  return probas_to_keep, bboxes_scaled

In [12]:
# COCO classes
CLASSES = [
    'N/A', 'person', 'bicycle', 'car', 'motorcycle', 'airplane', 'bus',
    'train', 'truck', 'boat', 'traffic light', 'fire hydrant', 'N/A',
    'stop sign', 'parking meter', 'bench', 'bird', 'cat', 'dog', 'horse',
    'sheep', 'cow', 'elephant', 'bear', 'zebra', 'giraffe', 'N/A', 'backpack',
    'umbrella', 'N/A', 'N/A', 'handbag', 'tie', 'suitcase', 'frisbee', 'skis',
    'snowboard', 'sports ball', 'kite', 'baseball bat', 'baseball glove',
    'skateboard', 'surfboard', 'tennis racket', 'bottle', 'N/A', 'wine glass',
    'cup', 'fork', 'knife', 'spoon', 'bowl', 'banana', 'apple', 'sandwich',
    'orange', 'broccoli', 'carrot', 'hot dog', 'pizza', 'donut', 'cake',
    'chair', 'couch', 'potted plant', 'bed', 'N/A', 'dining table', 'N/A',
    'N/A', 'toilet', 'N/A', 'tv', 'laptop', 'mouse', 'remote', 'keyboard',
    'cell phone', 'microwave', 'oven', 'toaster', 'sink', 'refrigerator', 'N/A',
    'book', 'clock', 'vase', 'scissors', 'teddy bear', 'hair drier',
    'toothbrush'
]

# colors for visualization
COLORS = [[0.000, 0.447, 0.741], [0.850, 0.325, 0.098], [0.929, 0.694, 0.125],
          [0.494, 0.184, 0.556], [0.466, 0.674, 0.188], [0.301, 0.745, 0.933]]

In [13]:
import matplotlib.pyplot as plt

def plot_results(pil_img, prob=None, boxes=None):
    plt.figure(figsize=(16,10))
    plt.imshow(pil_img)
    ax = plt.gca()
    colors = COLORS * 100
    if prob is not None and boxes is not None:
      for p, (xmin, ymin, xmax, ymax), c in zip(prob, boxes.tolist(), colors):
          ax.add_patch(plt.Rectangle((xmin, ymin), xmax - xmin, ymax - ymin,
                                    fill=False, color=c, linewidth=3))
          cl = p.argmax()
          text = f'{CLASSES[cl]}: {p[cl]:0.2f}'
          ax.text(xmin, ymin, text, fontsize=15,
                  bbox=dict(facecolor='yellow', alpha=0.5))
    plt.axis('off')
    plt.show()

In [15]:
from PIL import Image
import requests


## Clone  custom code of DETR

Clone (https://github.com/woctezuma/detr/tree/finetune) tailored for a custom dataset:
-   called `custom`,
-   with `max_class_id = 2` ([explanation](https://github.com/facebookresearch/detr/issues/108#issuecomment-650269223)).

**Caveat**: if you later use `first_class_index = 1` for your dataset, then it is fine. However, if you later use `first_class_index = 0`, then you will have to override the value of `max_class_id` (so that it is equal to 1) when calling `!python main.py`. My fork can do that.


In [18]:
%cd /content/

!rm -rf detr
!git clone https://github.com/woctezuma/detr.git

%cd detr/

!git checkout finetune

/content
Cloning into 'detr'...
remote: Enumerating objects: 239, done.
remote: Total 239 (delta 0), reused 0 (delta 0), pack-reused 239
Receiving objects: 100% (239/239), 284.61 KiB | 3.23 MiB/s, done.
Resolving deltas: 100% (131/131), done.
/content/detr
Branch 'finetune' set up to track remote branch 'finetune' from 'origin'.
Switched to a new branch 'finetune'


## Load pre-trained weights

Load a check-point (urls can be found [here](https://github.com/facebookresearch/detr#model-zoo)), then remove the classification head.

In [19]:
# Get pretrained weights
checkpoint = torch.hub.load_state_dict_from_url(
            url='https://dl.fbaipublicfiles.com/detr/detr-r50-e632da11.pth',
            map_location='cpu',
            check_hash=True)

# Remove class weights
del checkpoint["model"]["class_embed.weight"]
del checkpoint["model"]["class_embed.bias"]
del checkpoint["model"]["query_embed.weight"]

# Save
torch.save(checkpoint,
           'detr-r50_no-class-head.pth')

## Prepare the dataset for fine-tuning

Engineering Materials dataset is used for training


You can choose whether to start indexing categories with 0 or with 1.

This is a matter of taste, and it should not impact the performance of the algorithm.

Clone [my fork](https://github.com/woctezuma/VIA2COCO/tree/fixes) to convert annotations from VIA format to COCO format.

We expect the directory structure to be the following:
```
path/to/coco/
├ annotations/  # JSON annotations
│  ├ annotations/custom_train.json
│  └ annotations/custom_val.json
├ train2017/    # training images
└ val2017/      # validation images
```

## Check the dataset after it was pre-processed for fine-tuning

To verify the data loading is correct, let's visualize the annotations of randomly selected samples in the training set:
-   Demo of COCO API: https://github.com/cocodataset/cocoapi/blob/master/PythonAPI/pycocoDemo.ipynb

In [21]:
%matplotlib inline
import pycocotools.coco as coco
from pycocotools.coco import COCO
import numpy as np
import skimage.io as io
import matplotlib.pyplot as plt
import pylab
pylab.rcParams['figure.figsize'] = (10.0, 8.0)

In [22]:
dataDir='/content/data/custom/'
dataType='train2017'
annFile='{}annotations/custom_train.json'.format(dataDir)

In [23]:
# initialize COCO api for instance annotations
coco=COCO(annFile)

loading annotations into memory...
Done (t=0.81s)
creating index...
index created!


In [24]:
coco

In [25]:
# display COCO categories and supercategories
cats = coco.loadCats(coco.getCatIds())

nms=[cat['name'] for cat in cats]
print('Categories: {}'.format(nms))

nms = set([cat['supercategory'] for cat in cats])
print('Super-categories: {}'.format(nms))

Categories: ['misc_stuff', 'aac_blocks', 'adhesives', 'ahus', 'aluminium_frames_for_false_ceiling', 'chiller', 'concrete_mixer_machine', 'concrete_pump_(50%)', 'control_panel', 'cu_piping', 'distribution_transformer', 'dump_truck___tipper_truck', 'emulsion_paint', 'enamel_paint', 'fine_aggregate', 'fire_buckets', 'fire_extinguishers', 'glass_wool', 'grader', 'hoist', 'hollow_concrete_blocks', 'hot_mix_plant', 'hydra_crane', 'interlocked_switched_socket', 'junction_box', 'lime', 'marble', 'metal_primer', 'pipe_fittings', 'rcc_hume_pipes', 'refrigerant_gas', 'river_sand', 'rmc_batching_plant', 'rmu_units', 'sanitary_fixtures', 'skid_steer_loader_(bobcat)', 'smoke_detectors', 'split_units', 'structural_steel_-_channel', 'switch_boards_and_switches', 'texture_paint', 'threaded_rod', 'transit_mixer', 'vcb_panel', 'vitrified_tiles', 'vrf_units', 'water_tank', 'wheel_loader', 'wood_primer', 'banner', 'blanket', 'branch', 'bridge', 'building-other', 'bush', 'cabinet', 'cage', 'cardboard', 'car

In [26]:
cats

[{'id': 0, 'name': 'misc_stuff', 'supercategory': 'coco_thing'},
 {'id': 1, 'name': 'aac_blocks', 'supercategory': 'N/A'},
 {'id': 2, 'name': 'adhesives', 'supercategory': 'N/A'},
 {'id': 3, 'name': 'ahus', 'supercategory': 'N/A'},
 {'id': 4,
  'name': 'aluminium_frames_for_false_ceiling',
  'supercategory': 'N/A'},
 {'id': 5, 'name': 'chiller', 'supercategory': 'N/A'},
 {'id': 6, 'name': 'concrete_mixer_machine', 'supercategory': 'N/A'},
 {'id': 7, 'name': 'concrete_pump_(50%)', 'supercategory': 'N/A'},
 {'id': 8, 'name': 'control_panel', 'supercategory': 'N/A'},
 {'id': 9, 'name': 'cu_piping', 'supercategory': 'N/A'},
 {'id': 10, 'name': 'distribution_transformer', 'supercategory': 'N/A'},
 {'id': 11, 'name': 'dump_truck___tipper_truck', 'supercategory': 'N/A'},
 {'id': 12, 'name': 'emulsion_paint', 'supercategory': 'N/A'},
 {'id': 13, 'name': 'enamel_paint', 'supercategory': 'N/A'},
 {'id': 14, 'name': 'fine_aggregate', 'supercategory': 'N/A'},
 {'id': 15, 'name': 'fire_buckets', 's

In [27]:
# load and display image
catIds = coco.getCatIds(catNms=['aac_blocks', 'adhesives']);
print(catIds)
#imgIds = coco.getImgIds(catIds=catIds );
#print(imgIds)

[1, 2]


## Fine-tuning

-   Instructions appear in [a Github Gist](https://gist.github.com/woctezuma/e9f8f9fe1737987351582e9441c46b5d).

NB: There is a `--frozen_weights` argument. However,
i) I have yet to figure out how it is used,
ii) it is of no use for box detection. Indeed, "frozen training is meant for segmentation only" (as mentioned at this [line](https://github.com/facebookresearch/detr/blob/f4cdc542de34de771da8b9189742e5465f5220cd/main.py#L110) of the source-code).

### Boilerplate variables

**Caveat**: the parameter name `num_classes` is misleading. It is actually the ID which DETR will reserve for **its own** `no_object` class.

It should be set to one plus the highest class ID in your dataset.

For instance, if you have one class (balloon):
- if you used the index n°0 for this class, then `max_id = 0` and `num_classes = max_id+1 = 1`
- if you used the index n°1 for this class, then `max_id = 1` and `num_classes = max_id+1 = 2`

Reference: https://github.com/facebookresearch/detr/issues/108#issuecomment-650269223

In [32]:
first_class_index = 0

In [33]:
!ls /content

data
dataset_labels_super_categories.txt
detr
drive
engineering_processed_dataset_train_part1.zip
engineering_processed_dataset_train_part2.zip
engineering_processed_dataset_train_part3_1.zip
engineering_processed_dataset_train_part3_2.zip
engineering_processed_dataset_train_part4_1.tar.gz
engineering_processed_dataset_train_part4_2.tar.gz
engineering_processed_dataset_valid_annotation.zip
sample_data


## Create list of category names and category objects having attriutes id, name, subcategory 

In [34]:
! cp '/content/dataset_labels_super_categories.txt' /content/data/custom

In [35]:
categoryObjList = []
categoryNameList = []

lines = []
with open('/content/data/custom/dataset_labels_super_categories.txt') as f:
    lines = f.readlines()

for line in lines:
    fields = line.split('.')
    category_id = int(fields[0])
    label = fields[1][1:-1]
    catSubCat = label.split('::')
    categoryName = catSubCat[0]
    SubCategoryName = catSubCat[1]
    categoryNameList.append(categoryName)
    categoryObj = {
        "id": category_id, 
        "name":categoryName , 
        "supercategory": SubCategoryName
    }
    categoryObjList.append(categoryObj)

In [36]:
assert(first_class_index in [0, 1])

if first_class_index == 0:

  # There is one class, balloon, with ID n°0.

  num_classes = 140

  finetuned_classes = categoryNameList


  # The `no_object` class will be automatically reserved by DETR with ID equal
  # to `num_classes`, so ID n°1 here.  

else:

  # There is one class, balloon, with ID n°1.
  #
  # However, DETR assumes that indexing starts with 0, as in computer science,
  # so there is a dummy class with ID n°0.
  # Caveat: this dummy class is not the `no_object` class reserved by DETR.

  num_classes = 141
  finetuned_classes = ['N/A']
  finetuned_classes.extend(categoryNameList)

  # The `no_object` class will be automatically reserved by DETR with ID equal
  # to `num_classes`, so ID n°2 here.

print('First class index: {}'.format(first_class_index))  
print('Parameter num_classes: {}'.format(num_classes))
print('Fine-tuned classes: {}'.format(finetuned_classes))

First class index: 0
Parameter num_classes: 140
Fine-tuned classes: ['misc_stuff', 'aac_blocks', 'adhesives', 'ahus', 'aluminium_frames_for_false_ceiling', 'chiller', 'concrete_mixer_machine', 'concrete_pump_(50%)', 'control_panel', 'cu_piping', 'distribution_transformer', 'dump_truck___tipper_truck', 'emulsion_paint', 'enamel_paint', 'fine_aggregate', 'fire_buckets', 'fire_extinguishers', 'glass_wool', 'grader', 'hoist', 'hollow_concrete_blocks', 'hot_mix_plant', 'hydra_crane', 'interlocked_switched_socket', 'junction_box', 'lime', 'marble', 'metal_primer', 'pipe_fittings', 'rcc_hume_pipes', 'refrigerant_gas', 'river_sand', 'rmc_batching_plant', 'rmu_units', 'sanitary_fixtures', 'skid_steer_loader_(bobcat)', 'smoke_detectors', 'split_units', 'structural_steel_-_channel', 'switch_boards_and_switches', 'texture_paint', 'threaded_rod', 'transit_mixer', 'vcb_panel', 'vitrified_tiles', 'vrf_units', 'water_tank', 'wheel_loader', 'wood_primer', 'banner', 'blanket', 'branch', 'bridge', 'build

In [37]:
%cd /content/detr/

/content/detr


In [38]:
! ls

d2			    engine.py	models		      test_all.py
datasets		    hubconf.py	README.md	      tox.ini
detr-r50_no-class-head.pth  LICENSE	requirements.txt      util
Dockerfile		    main.py	run_with_submitit.py


**Caveat**: below, we override the value of `num_classes` (hard-coded to 2 for the `custom` dataset in my `finetune` branch of DETR) in case `first_class_index = 0` instead of `first_class_index = 1` (default value).

## Perform training

In [ ]:
!python main.py \
  --dataset_file "custom" \
  --coco_path "/content/data/custom/" \
  --output_dir "/content/drive/My Drive/eva6_capstone_final/outputs" \
  --resume "detr-r50_no-class-head.pth" \
  --num_classes $num_classes \
  --epochs 25 \
  --lr 1e-5 \
  --num_queries 30 \
  --batch_size 2

Streaming output truncated to the last 5000 lines.
Epoch: [6]  [1770/6835]  eta: 1:17:09  lr: 0.000010  class_error: 33.33  loss: 14.5129 (17.7975)  loss_ce: 1.2804 (1.6680)  loss_bbox: 0.5067 (0.6607)  loss_giou: 0.3365 (0.5222)  loss_ce_0: 1.5161 (1.9033)  loss_bbox_0: 0.5618 (0.7185)  loss_giou_0: 0.5034 (0.5650)  loss_ce_1: 1.3576 (1.8185)  loss_bbox_1: 0.4909 (0.6813)  loss_giou_1: 0.4445 (0.5386)  loss_ce_2: 1.3864 (1.7471)  loss_bbox_2: 0.5152 (0.6703)  loss_giou_2: 0.3424 (0.5295)  loss_ce_3: 1.3008 (1.7120)  loss_bbox_3: 0.5233 (0.6650)  loss_giou_3: 0.3964 (0.5253)  loss_ce_4: 1.3688 (1.6886)  loss_bbox_4: 0.5005 (0.6610)  loss_giou_4: 0.3592 (0.5226)  loss_ce_unscaled: 1.2804 (1.6680)  class_error_unscaled: 50.0000 (60.8339)  loss_bbox_unscaled: 0.1013 (0.1321)  loss_giou_unscaled: 0.1682 (0.2611)  cardinality_error_unscaled: 2.0000 (2.8010)  loss_ce_0_unscaled: 1.5161 (1.9033)  loss_bbox_0_unscaled: 0.1124 (0.1437)  loss_giou_0_unscaled: 0.2517 (0.2825)  cardinality_error_0

In [40]:
! ls -l /content/data/custom/val2017

total 551796
-rw-r--r-- 1 root root   34222 Sep  8 01:05  aac_blocks_110.jpg
-rw-r--r-- 1 root root   12795 Sep  8 01:05  aac_blocks_122.jpg
-rw-r--r-- 1 root root   30181 Sep  8 01:05  aac_blocks_128.jpg
-rw-r--r-- 1 root root   61180 Sep  8 01:05  aac_blocks_198.jpg
-rw-r--r-- 1 root root  261856 Sep  8 01:05  aac_blocks_209.jpg
-rw-r--r-- 1 root root    9993 Sep  8 01:05  aac_blocks_239.jpg
-rw-r--r-- 1 root root    5066 Sep  8 01:05  adhesives_279.jpg
-rw-r--r-- 1 root root   10189 Sep  8 01:05  adhesives_288.jpg
-rw-r--r-- 1 root root   12908 Sep  8 01:05  adhesives_315.jpg
-rw-r--r-- 1 root root   14344 Sep  8 01:05  adhesives_332.jpg
-rw-r--r-- 1 root root   85357 Sep  8 01:05  adhesives_334.jpg
-rw-r--r-- 1 root root  106416 Sep  8 01:05  adhesives_350.jpg
-rw-r--r-- 1 root root   99276 Sep  8 01:05  adhesives_356.jpg
-rw-r--r-- 1 root root  136399 Sep  8 01:05  adhesives_360.jpg
-rw-r--r-- 1 root root   52940 Sep  8 01:05  ahus_375.jpg
-rw-r--r-- 1 root root    6471 Sep  8 01:

## Check the results

### Monitoring of training

Reference: https://github.com/lessw2020/Thunder-Detr/blob/master/View_your_training_results.ipynb

In [41]:
from util.plot_utils import plot_logs

from pathlib import Path

log_directory = [Path('outputs/')]

As mentioned in the code of [`plot_logs`](https://github.com/facebookresearch/detr/blob/5e66b4cd15b2b182da347103dd16578d28b49d69/util/plot_utils.py#L13):
-   solid lines are training results,
-   dashed lines are validation results.

In [42]:
fields_of_interest = (
    'loss',
    'mAP',
    )

plot_logs(log_directory,
          fields_of_interest)

ValueError: ignored

In [ ]:
fields_of_interest = (
    'loss_ce',
    'loss_bbox',
    'loss_giou',
    )

plot_logs(log_directory,
          fields_of_interest)

In [ ]:
fields_of_interest = (
    'class_error',
    'cardinality_error_unscaled',
    )

plot_logs(log_directory,
          fields_of_interest)   

### Load the fine-tuned model

- How to replace the classification head: https://github.com/facebookresearch/detr/issues/9#issuecomment-636391562

In [ ]:
model = torch.hub.load('facebookresearch/detr',
                       'detr_resnet50',
                       pretrained=False,
                       num_classes=num_classes)

checkpoint = torch.load('outputs/checkpoint.pth',
                        map_location='cpu')

model.load_state_dict(checkpoint['model'],
                      strict=False)

model.eval();

### Boilerplate functions to display fine-tuned results

In [ ]:
def plot_finetuned_results(pil_img, prob=None, boxes=None):
    plt.figure(figsize=(16,10))
    plt.imshow(pil_img)
    ax = plt.gca()
    colors = COLORS * 100
    if prob is not None and boxes is not None:
      for p, (xmin, ymin, xmax, ymax), c in zip(prob, boxes.tolist(), colors):
          ax.add_patch(plt.Rectangle((xmin, ymin), xmax - xmin, ymax - ymin,
                                    fill=False, color=c, linewidth=3))
          cl = p.argmax()
          text = f'{finetuned_classes[cl]}: {p[cl]:0.2f}'
          ax.text(xmin, ymin, text, fontsize=15,
                  bbox=dict(facecolor='yellow', alpha=0.5))
    plt.axis('off')
    plt.show()

In [ ]:
def run_worflow(my_image, my_model):
  # mean-std normalize the input image (batch-size: 1)
  img = transform(my_image).unsqueeze(0)

  # propagate through the model
  outputs = my_model(img)

  for threshold in [0.9, 0.7]:
    
    probas_to_keep, bboxes_scaled = filter_bboxes_from_outputs(outputs,
                                                              threshold=threshold)

    plot_finetuned_results(my_image,
                           probas_to_keep, 
                           bboxes_scaled)


In [ ]:
ls -l '/content/data/custom/train2017'

In [ ]:
ls -l '/content/data/custom/val2017'

### With a training image

In [ ]:
from PIL import Image

img_name = '/content/data/custom/train2017/aac_blocks_180.jpg'
im = Image.open(img_name)

run_worflow(im,
            model)

### With a validation image

In [ ]:
from PIL import Image

img_name = '/content/data/custom/val2017/adhesives_307.jpg'
im = Image.open(img_name)

run_worflow(im,
            model)